<a href="https://colab.research.google.com/github/yyyyyokoko/AI-class/blob/master/data_characterization/MAG/Luwei's_MAG_Affiliations_Report.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Characterization Report for Affiliations**


In [ ]:
#@title
import pandas as pd
import re
import numpy as np
import plotly.io as pio
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots

from datetime import date
from google.cloud import bigquery
from IPython.display import display, HTML
from google.colab import auth

auth.authenticate_user()
client = bigquery.Client(project="gcp-cset-projects")

In [ ]:
import warnings
warnings.filterwarnings('ignore')

In [ ]:
# you can use pandas for these "data characterization reports" if you wish. Here's an example of how to load a table's data into a dataframe.
affiliations = pd.read_gbq("select * from gcp_cset_mag.Affiliations", dialect="standard", project_id="gcp-cset-projects")

# and here's an example of how to load a table's data into a list, if you'd rather not use pandas
# client = bigquery.Client(project="gcp-cset-projects")
# data = [row for row in client.query("select * from gcp_cset_mag.ConferenceInstances")]

In [ ]:
affiliations

AffiliationId   Rank  ... CreatedDate         import_time
0         3006269982  19380  ...  2020-02-24 2020-06-06 13:46:37
1         3017153554  19380  ...  2020-04-24 2020-06-06 13:46:37
2          173894486  13564  ...  2016-06-24 2020-06-06 13:46:37
3           79211490  13530  ...  2016-06-24 2020-06-06 13:46:37
4          184256567  13217  ...  2016-06-24 2020-06-06 13:46:37
...              ...    ...  ...         ...                 ...
25754     2956445460  18687  ...  2019-07-23 2020-06-06 13:46:37
25755     2958956727  17534  ...  2019-07-23 2020-06-06 13:46:37
25756     2960094004   9275  ...  2019-07-23 2020-06-06 13:46:37
25757     2960998687  12094  ...  2019-07-23 2020-06-06 13:46:37
25758     2961216182   9432  ...  2019-07-23 2020-06-06 13:46:37

[25759 rows x 14 columns]

In [ ]:
finalDF = pd.DataFrame(columns=['Colname', 'Has Null?', 'Possible Null Values', '# of Null Values', 'Has Unique Values?', 'Original Data Type', 
                                'Suggested Data Type', 'Note', 'Normalization Ideas'])
finalDF.Colname = affiliations.columns[:-1]
finalDF['Possible Null Values'] = ''
finalDF['# of Null Values'] = 0
finalDF['Note'] = ''
finalDF['Normalization Ideas'] = ''   

In [ ]:
def checkUniqueness(df):
  nrow = len(df)
  print("Total number of rows: ", nrow)
  for i in df.columns[:-1]:
    a = len(df[i].unique())
    if a == nrow:
      print("Unique:", i)
      finalDF.loc[finalDF.Colname == i, 'Has Unique Values?'] = 'Yes'
    else:
      print('Number of unique values of', i, 'is:', sum(df[i].value_counts() == 1))
      finalDF.loc[finalDF.Colname == i, 'Has Unique Values?'] = 'No'
  return
checkUniqueness(affiliations)

Total number of rows:  25759
Unique: AffiliationId
Number of unique values of Rank is: 3108
Number of unique values of NormalizedName is: 25675
Unique: DisplayName
Number of unique values of GridId is: 18962
Number of unique values of OfficialPage is: 16977
Number of unique values of WikiPage is: 25450
Number of unique values of PaperCount is: 3602
Number of unique values of PaperFamilyCount is: 3516
Number of unique values of CitationCount is: 9101
Number of unique values of Latitude is: 22359
Number of unique values of Longitude is: 22526
Number of unique values of CreatedDate is: 19


In [ ]:
#check NA
def checkNA(df, finalDF):
  possible_na = ['na', 'NA', 'tbd', 'TBD', 'n/a', 'N/A', 'Null', 'null', 'NULL', 'none', 'None', 'NONE', 'tba', 'TBA']
  for i in df.columns[:-1]:
    if df[i].dtypes == np.object:
      #number of empty string
      empty = sum(df[i].str.contains(r'^\s*$'))
      if empty != 0:
        finalDF.loc[finalDF.Colname == i, 'Has Null?'] = 'Yes'
        finalDF.loc[finalDF.Colname == i, 'Possible Null Values'] = finalDF.loc[finalDF.Colname == i, 'Possible Null Values'] + 'empty string'
        finalDF.loc[finalDF.Colname == i, '# of Null Values'] += empty
      #number of NA,TBD,n/a,null,none,TBA
      for j in possible_na:
        temp = sum(df[i].str.strip() == j)
        if temp != 0:
          finalDF.loc[finalDF.Colname == i, 'Has Null?'] = 'Yes'
          finalDF.loc[finalDF.Colname == i, 'Possible Null Values'] = finalDF.loc[finalDF.Colname == i, 'Possible Null Values'] +', ' + j 
          finalDF.loc[finalDF.Colname == i, '# of Null Values'] += temp
      #np.nan
      real_na = sum(df[i].isnull())
      if real_na != 0:
        finalDF.loc[finalDF.Colname == i, 'Has Null?'] = 'Yes'
        finalDF.loc[finalDF.Colname == i, 'Possible Null Values'] = finalDF.loc[finalDF.Colname == i, 'Possible Null Values'] +', np.nan' 
        finalDF.loc[finalDF.Colname == i, '# of Null Values'] += real_na
    else:
      #np.nan
      real_na = sum(df[i].isnull())
      if real_na == 0:
        finalDF.loc[finalDF.Colname == i, 'Has Null?'] = 'No'
      else:
        finalDF.loc[finalDF.Colname == i, 'Possible Null Values'] = 'np.nan'
        finalDF.loc[finalDF.Colname == i, 'Has Null?'] = 'Yes'
        finalDF.loc[finalDF.Colname == i, '# of Null Values'] += real_na
  finalDF['Has Null?'] = finalDF['Has Null?'].fillna('No')
  return finalDF
finalDF = checkNA(affiliations, finalDF)

In [ ]:
#check the format of GridId
count = 0
lst_index = []
for i in range(len(affiliations.GridId)):
  if affiliations.GridId[i] != "":
    x = re.search("^(grid[.]\w+[.]\w+)$", affiliations.GridId[i])
    if x: pass
    else: 
      count += 1
      lst_index.append(i)

In [ ]:
finalDF['Suggested Data Type'] = ['INTEGER', 'INTEGER', 'STRING', 'STRING', 'STRING', 'STRING', 'STRING', 'INTEGER', 'INTEGER', 'INTEGER', 'FLOAT', 'FLOAT', 'DATETIME']   
finalDF['Original Data Type'] = ['INTEGER', 'INTEGER', 'STRING', 'STRING', 'STRING', 'STRING', 'STRING', 'INTEGER', 'INTEGER', 'INTEGER', 'STRING', 'STRING', 'DATETIME'] 
finalDF.loc[finalDF['Colname'] == 'NormalizedName', 'Note'] = 'Close to unique'
finalDF.loc[finalDF['Colname'] == 'WikiPage', 'Note'] = 'Close to unique'

## **Report Overview**

In [ ]:
finalDF

Colname Has Null?  ...             Note  Normalization Ideas
0      AffiliationId        No  ...                                      
1               Rank        No  ...                                      
2     NormalizedName        No  ...  Close to unique                     
3        DisplayName        No  ...                                      
4             GridId       Yes  ...                                      
5       OfficialPage       Yes  ...                                      
6           WikiPage       Yes  ...  Close to unique                     
7         PaperCount        No  ...                                      
8   PaperFamilyCount        No  ...                                      
9      CitationCount        No  ...                                      
10          Latitude       Yes  ...                                      
11         Longitude       Yes  ...                                      
12       CreatedDate        No  ...                                      

[13 rows x 9 columns]

1. Some institutions such as Harvard University, Max Planck Society have very large **PaperCount, PaperFamilyCount** and **CitationCount**. These records are indicated below.
2. Change the data types of **Latitude** and **Longitude** to float. 
3. While most of the **Rank** values follow a normal distribution, some records have Rank value greater than 19300. This might need furthur investigation. 
4. Replace the empty strings with null.

## **Graphs**


In [ ]:
#rank distribution
fig1 = px.histogram(affiliations, x="Rank", title='Histogram of AffiliationId counts by Rank')
fig1.show()

In [ ]:
#Outlier investigation for Ranks greater than 19300
affiliations.loc[affiliations['Rank'] > 19300, :]

AffiliationId   Rank  ... CreatedDate         import_time
0         3006269982  19380  ...  2020-02-24 2020-06-06 13:46:37
1         3017153554  19380  ...  2020-04-24 2020-06-06 13:46:37
43         908752181  19380  ...  2016-06-24 2020-06-06 13:46:37
44         161831233  19380  ...  2016-06-24 2020-06-06 13:46:37
46         913647346  19380  ...  2016-06-24 2020-06-06 13:46:37
...              ...    ...  ...         ...                 ...
25736     3004375662  19380  ...  2020-02-07 2020-06-06 13:46:37
25737     3003279638  19342  ...  2020-02-07 2020-06-06 13:46:37
25740     3011239886  19380  ...  2020-03-23 2020-06-06 13:46:37
25741     3011266249  19380  ...  2020-03-23 2020-06-06 13:46:37
25742     3010696794  19380  ...  2020-03-23 2020-06-06 13:46:37

[416 rows x 14 columns]

In [ ]:
#paper count distribution
fig2 = px.histogram(affiliations, x="PaperCount", title='Histogram of AffiliationId counts by PaperCount')
fig2.show()

In [ ]:
#Outlier investigation for PaperCount greater than 380000
affiliations.loc[affiliations.PaperCount >= 380000,:]

AffiliationId  Rank  ... CreatedDate         import_time
584        136199984  4410  ...  2016-06-24 2020-06-06 13:46:37
1371        19820366  5419  ...  2016-06-24 2020-06-06 13:46:37
2780      1294671590  5288  ...  2016-06-24 2020-06-06 13:46:37
11913      149899117  5006  ...  2016-06-24 2020-06-06 13:46:37

[4 rows x 14 columns]

In [ ]:
#PaperFamilyCount
fig3 = px.histogram(affiliations, x="PaperFamilyCount", title='Histogram of AffiliationId counts by PaperFamilyCount')
fig3.show()

In [ ]:
#Outlier investigation for PaperFamilyCount greater than 380000
affiliations.loc[affiliations.PaperFamilyCount >= 370000, :]

AffiliationId  Rank  ... CreatedDate         import_time
584        136199984  4410  ...  2016-06-24 2020-06-06 13:46:37
1371        19820366  5419  ...  2016-06-24 2020-06-06 13:46:37
2780      1294671590  5288  ...  2016-06-24 2020-06-06 13:46:37
11913      149899117  5006  ...  2016-06-24 2020-06-06 13:46:37

[4 rows x 14 columns]

In [ ]:
#Citation Count
fig4 = px.histogram(affiliations, x="CitationCount", title='Histogram of AffiliationId counts by CitationCount')
fig4.show()

In [ ]:
#outlier investigation 
affiliations.loc[affiliations.CitationCount >= 13000000, :]

AffiliationId  Rank  ... CreatedDate         import_time
584        136199984  4410  ...  2016-06-24 2020-06-06 13:46:37
9116        97018004  4917  ...  2016-06-24 2020-06-06 13:46:37
11913      149899117  5006  ...  2016-06-24 2020-06-06 13:46:37
17885     1299303238  5055  ...  2016-06-24 2020-06-06 13:46:37

[4 rows x 14 columns]

In [ ]:
# "Latitude", "Longitude" by color
temp2 = affiliations.loc[:,["Latitude", "Longitude", "DisplayName"]]
temp2['Latitude'] = pd.to_numeric(temp2['Latitude'])
temp2['Longitude'] = pd.to_numeric(temp2['Longitude'])
temp2 = temp2.round(1)
temp2['Color'] = temp2['DisplayName'].astype('category').cat.codes

fig = go.Figure()
fig.add_trace(go.Scattergeo(
    lon = temp2['Longitude'],
    lat = temp2['Latitude'],
    text = temp2['DisplayName'],
    marker_color = temp2['Color']
    ))
fig.update_layout(title_text = 'Map of Affiliations locations, rounded')


In [ ]:
# "Latitude", "Longitude" by Count size
# For the locations that have more than three institutions, the map only displays three names in hovertext
temp2 = affiliations.loc[:,["Latitude", "Longitude", "DisplayName"]]
temp2['Latitude'] = pd.to_numeric(temp2['Latitude'])
temp2['Longitude'] = pd.to_numeric(temp2['Longitude'])
temp2 = temp2.round(1)

temp = pd.DataFrame(temp2.groupby(["Latitude", "Longitude"]).size()).reset_index()
temp.columns = ["Latitude", "Longitude", "Count"]
temp.replace('', np.nan, inplace=True) 
temp = temp.dropna()
temp['text'] = np.nan

for i in range(len(temp)):
  lat = temp.Latitude[i]
  lon = temp.Longitude[i]
  name_lst = temp2.loc[(temp2.Latitude == lat) & (temp2.Longitude == lon), 'DisplayName'].values
  if len(name_lst) >= 3:
    name_lst = name_lst[0:3]
  temp['text'][i] = name_lst

temp['text'] = temp['text'].str.join(', ')
temp['text'] = temp['text'] + '<br>' + 'Count = ' + temp['Count'].astype(str)

fig = go.Figure()
fig.add_trace(go.Scattergeo(
    lon = temp['Longitude'],
    lat = temp['Latitude'],
    text = temp['text'],
    marker = dict(
        size = temp['Count'],
        line_color='rgb(40,40,40)',
        line_width=0.5,
        sizemode = 'area'
    )))
fig.update_layout(title_text = 'Map of Affiliations locations by count, rounded')

In [ ]:
temp3 = affiliations.loc[:,["Latitude", "Longitude", "DisplayName"]]
temp = pd.DataFrame(temp3.groupby(["Latitude", "Longitude"]).size()).reset_index()
temp.columns = ["Latitude", "Longitude", "Count"]
temp.replace('', np.nan, inplace=True)
temp = temp.dropna().reset_index()
temp['text'] = np.nan
#temp3['text'] = 'Count = ' + temp3['Count'].astype(str)

for i in range(len(temp)):
  lat = temp.Latitude[i]
  lon = temp.Longitude[i]
  name_lst = temp3.loc[(temp3.Latitude == lat) & (temp3.Longitude == lon), 'DisplayName'].values
  if len(name_lst) >= 3:
    name_lst = name_lst[0:3]
  temp['text'][i] = name_lst

temp['text'] = temp['text'].str.join(', ')
temp['text'] = temp['text'] + '<br>' + 'Count = ' + temp['Count'].astype(str)


fig5 = go.Figure()
fig5.add_trace(go.Scattergeo(
    lon = temp['Longitude'],
    lat = temp['Latitude'],
    text = temp['text'],
    marker = dict(
        size = temp['Count'],
        line_color='rgb(40,40,40)',
        line_width=0.5,
        sizemode = 'area'
    )))
fig5.update_layout(title_text = 'Map of Affiliations by counts')